[![Open In Colab](https://colab.research.google.com/assets/colab-badge.svg)](https://colab.research.google.com/drive/1dafl_LF6riOwa7h9Qd5xxW4TTYigpepk?usp=sharing)

# StockBacktesting

This notebook demonstrates using the ``backtesting.py`` library to test trading strategies.

The process has two main parts:




*   **Single Ticker Backtesting**: Test the strategy on one stock or asset. The settings can be adjusted and see detailed charts and results.
*   **Automated Backtesting**: Quickly testing the strategy on many stocks at once. This uses multiple processors to run faster and helps find the best stocks to trade.

This way, we can understand the strategies well on one stock, then apply it to many stocks easily.




# Table of Contents

* [Basic Preparation](#Basic-Preparation)
* [Single Ticker Backtesting](#Single-Ticker-Backtesting)
  * [Configuration](#Configuration)
  * [Data Downloading](#Data-Downloading)
  * [Strategy 1](#Strategy-1)
    * [Define Strategy](#Define-Strategy)
    * [Optimize](#Optimize)
    * [Run](#Run)
* [Automated Backtesting](#Automated-Backtesting)
  * [Download a List of Tickers Data](#Download-a-List-of-Tickers-Data)
  * [Optional: Filtering](#Optional:-Filtering)
  * [Iteratively Running: Multi Processing](#Iteratively-Running:-Multi-Processing)
    * [Strategy 1](#Strategy-1)
      * [Define Strategy](#Define-Strategy)
      * [Auto Processing](#Auto-Processing)
  * [Example Results](#Example-Results)

# Basic Preparation

In [ ]:
%%capture
try:
    import backtesting
except ImportError:
    !pip install git+https://github.com/kernc/backtesting.py.git@master
    !pip install --upgrade bokeh
    url = 'https://anaconda.org/conda-forge/libta-lib/0.4.0/download/linux-64/libta-lib-0.4.0-h166bdaf_1.tar.bz2'
    !curl -L $url | tar xj -C /usr/lib/x86_64-linux-gnu/ lib --strip-components=1
    url = 'https://anaconda.org/conda-forge/ta-lib/0.5.1/download/linux-64/ta-lib-0.5.1-py311h9ecbd09_0.conda'
    !curl -L $url -o /content/ta-lib.conda
    !mkdir /content/ta-lib
    !unzip /content/ta-lib.conda -d /content/ta-lib
    !sudo apt-get install zstd
    !tar --zstd -xvf /content/ta-lib/pkg-ta-lib-0.5.1-py311h9ecbd09_0.tar.zst lib/python3.11/site-packages/talib --strip-components=3
    !rm -rf /content/ta-lib.conda /content/ta-lib
    import talib
    import os
    ! pip install sambo
    os.kill(os.getpid(), 9)
finally:
    from backtesting import Strategy, Backtest
    from backtesting.lib import crossover, TrailingStrategy,cross
    import yfinance as yf
    from datetime import datetime
    import pandas as pd
    import talib
    import numpy as np
    from multiprocessing import Pool
    import multiprocessing
    import os
    import shutil

# Single Ticker Backtesting

## Configuration
Define the ticker, start and end dates for data download, and backtesting optimization settings.

We will use

```python
class Config:
```

to setup the configuration

In [ ]:
class Config:
    # Download Settings
    ticker = "AAPL"
    start = "2024-01-01"
    end = pd.Timestamp.today()

    # Backtesting Optimization Settings
    cash = 10_000
    finalize_trades = True
    maximize = 'Equity Final [$]'
    method = 'sambo'
    max_tries = 10000
    random_state=0
    return_heatmap=True
    return_optimization=True

## Data Downloading

In [ ]:
def prepare_yfinance_df(df):
    """
    Converts the index of a Yahoo Finance DataFrame to datetime
    and removes the multi-level column index if present.

    Args:
        df (pd.DataFrame): The DataFrame downloaded from yfinance.

    Returns:
        pd.DataFrame: The processed DataFrame with a datetime index.
    """
    import pandas as pd
    # Convert index to DatetimeIndex
    df.index = pd.to_datetime(df.index)
    # Remove multi-level column index if present
    if isinstance(df.columns, pd.MultiIndex):
        df.columns = df.columns.droplevel(1)
    return df

df = yf.download( Config.ticker, Config.start, Config.end)
df1 = prepare_yfinance_df(df).copy()

/tmp/ipython-input-1103549413.py:20: FutureWarning: YF.download() has changed argument auto_adjust default to True
  df = yf.download( Config.ticker, Config.start, Config.end)
[*********************100%***********************]  1 of 1 completed


In [ ]:
df1

Price            Close        High         Low        Open    Volume
Date                                                                
2024-01-02  184.290405  187.070052  182.553128  185.789422  82488700
2024-01-03  182.910522  184.528677  182.096477  182.880742  58414500
2024-01-04  180.587540  181.758954  179.565029  180.825785  71983600
2024-01-05  179.862823  181.431339  178.860172  180.666948  62379700
2024-01-08  184.210999  184.250716  180.180517  180.766224  59144500
...                ...         ...         ...         ...       ...
2025-07-25  213.880005  215.240005  213.399994  214.699997  40268800
2025-07-28  214.050003  214.850006  213.059998  214.029999  37858000
2025-07-29  211.270004  214.809998  210.820007  214.179993  51411700
2025-07-30  209.050003  212.389999  207.720001  211.899994  43797200
2025-07-31  208.820007  209.839996  207.824997  208.380005  27442594

[396 rows x 5 columns]

## Strategy 1

### Define Strategy

Define your trading strategy by creating a class that inherits from `backtesting.Strategy` (or a similar class like `TrailingStrategy`). This class includes:


*   Parameters for technical indicators (e.g., MACD, Bollinger Bands, RSI).
*   An `init()` method to calculate the indicators.
*   A `next()` method to define the buy and sell signals based on the indicators.

In [ ]:
class MyStrategy(TrailingStrategy):
    MACD_fast_period = 12
    MACD_slow_period = 26
    MACD_signal_period = 9

    BB_n_periods = 20
    BB_n_std_for_long = 2
    BB_n_std_for_short = 2

    RSI_n_periods = 14

    RSI_overbought_threshold = 80
    use_BB_for_long = 1
    use_BB_for_short = 1
    use_RSI_for_SHORT = 1
    use_RSI_for_LONG = 1
    use_MACD_for_LONG = 1
    use_MACD_for_SHORT = 1
    trailing_sl_ATR = 2  # Example trailing stop ATR multiplier

    def init(self):
        super().init()
        # MACD Calculation
        self.macd, self.macd_signal, self.macd_hist = self.I(talib.MACD, self.data.Close,
                                                             fastperiod=self.MACD_fast_period,
                                                             slowperiod=self.MACD_slow_period,
                                                             signalperiod=self.MACD_signal_period,
                                                             plot = False
                                                             )
        self.upper, self.middle, self.lower = self.I(talib.BBANDS, self.data.Close,
                                                    timeperiod=self.BB_n_periods,
                                                    nbdevup=self.BB_n_std_for_short,
                                                    nbdevdn=self.BB_n_std_for_long,
                                                    plot = True)
        def get_user_macd(macd, macd_signal, macd_hist):
            return macd, macd_signal, macd_hist
        self.macd, self.macd_signal, self.macd_hist = self.I(get_user_macd, self.macd, self.macd_signal, self.macd_hist)
        # Calculate RSI
        self.rsi = self.I(talib.RSI, self.data.Close, timeperiod=self.RSI_n_periods)

        self.FINAL_SIGNAL = None  # For debugging/analysis

    def next(self):
        super().next()
        # Buy when MACD signal crosses BELOW lower Bollinger Band
        macd_buy = self.macd_signal[-1] < self.lower[-1]

        # Sell when MACD signal crosses ABOVE upper Bollinger Band
        macd_sell = self.macd_signal[-1] > self.lower[-1]
        BB_buy = self.data.Close[-1] > self.upper[-1]
        BB_sell = self.data.Close[-1] < self.lower[-1]

        rsi_overbought = self.rsi[-1] > self.RSI_overbought_threshold
        rsi_oversold = self.rsi[-1] < 20

        buy_signal = (
            (self.use_MACD_for_LONG and macd_buy) or
            (self.use_BB_for_long and BB_buy) or
            (self.use_RSI_for_LONG and rsi_oversold)
            )

        sell_signal = (
            (self.use_MACD_for_SHORT and macd_sell) or
            (self.use_BB_for_short and BB_sell) or
            (self.use_RSI_for_SHORT and rsi_overbought)
        )

        if self.position:
            if sell_signal:
                self.position.close()
                self.FINAL_SIGNAL = -1  # Mark as sell
        elif buy_signal:
            self.buy()
            self.FINAL_SIGNAL = 1  # Mark as buy

        if self.position:  # Only set trailing stop if in a position
            self.set_trailing_sl(self.trailing_sl_ATR)  # Set trailing stop loss

### Optimize

This step optimizes the parameters of the `MyStrategy` using the `Backtest.optimize()` method. The optimization aims to find the best combination of parameters that maximizes the `'Equity Final [$]'` metric. The `sambo` method is used for optimization with a specified number of maximum tries and a random state for reproducibility. The results include the best performing parameters, a heatmap of results, and the optimization details.

In [ ]:
bt1 = Backtest(df1, MyStrategy, cash=Config.cash, finalize_trades = Config.finalize_trades)
stats, heatmap, optimize_result = bt1.optimize(
    MACD_fast_period = range(12, 23, 2),
    MACD_slow_period = range(24,35, 2),
    MACD_signal_period = range(3,10,1),

    BB_n_periods = range(15,25,2),
    BB_n_std_for_long = np.arange(1, 3.1, 0.1),
    BB_n_std_for_short = np.arange(1, 3.1, 0.1),
    RSI_n_periods = np.arange(14,16,1),
    RSI_overbought_threshold = np.arange(75, 96, 5),

    use_BB_for_long = [1,0],
    use_BB_for_short = [1,0],
    use_RSI_for_SHORT = [1,0],
    use_MACD_for_LONG = [1],
    use_MACD_for_SHORT = [1],
    trailing_sl_ATR = [2,3,4,5],
    maximize=Config.maximize,
    method=Config.method,
    max_tries=Config.max_tries,
    random_state=Config.random_state,
    return_heatmap=Config.return_heatmap,
    return_optimization=Config.return_optimization,
)

Backtest.optimize:   0%|          | 0/10000 [00:00<?, ?it/s]

Backtest.run:   0%|          | 0/361 [00:00<?, ?bar/s]

Backtest.run:   0%|          | 0/358 [00:00<?, ?bar/s]

Backtest.run:   0%|          | 0/358 [00:00<?, ?bar/s]

Backtest.run:   0%|          | 0/365 [00:00<?, ?bar/s]

...

Backtest.run:   0%|          | 0/354 [00:00<?, ?bar/s]

Backtest.run:   0%|          | 0/354 [00:00<?, ?bar/s]

Backtest.run:   0%|          | 0/354 [00:00<?, ?bar/s]

Backtest.run:   0%|          | 0/354 [00:00<?, ?bar/s]

Backtest.run:   0%|          | 0/354 [00:00<?, ?bar/s]

In [ ]:
heatmap.sort_values().iloc[-10:]

MACD_fast_period  MACD_slow_period  MACD_signal_period  BB_n_periods  BB_n_std_for_long  BB_n_std_for_short  RSI_n_periods  RSI_overbought_threshold  use_BB_for_long  use_BB_for_short  use_RSI_for_SHORT  use_MACD_for_LONG  use_MACD_for_SHORT  trailing_sl_ATR
22                34                9                   22            2.476066           3.000000            14             77                        0                1                 0                  1                  1                   5                  14855.950931
                                                                      2.477064           3.000000            14             80                        0                1                 0                  1                  1                   5                  14855.950931
                                                                      2.477628           3.000000            14             79                        0                1                 0                  1                  1                   5                  14855.950931
                                                                      2.468561           3.000000            14             76                        0                1                 0                  1                  1                   5                  14855.950931
                                                                      2.470591           3.000000            14             79                        0                1                 0                  1                  1                   5                  14855.950931
20                34                9                   21            2.496318           2.859564            14             79                        0                1                 0                  1                  1                   5                  14855.950931
22                34                9                   21            2.532054           3.000000            14             84                        0                1                 0                  1                  1                   5                  14855.950931
                                                                      2.635187           3.000000            14             77                        0                1                 0                  1                  1                   5                  14855.950931
                                                                      2.629177           3.000000            14             77                        0                1                 0                  1                  1                   5                  14855.950931
                                                                      2.605411           3.000000            14             77                        0                1                 0                  1                  1                   5                  14855.950931
Name: Equity Final [$], dtype: float64

In [ ]:
stats._strategy._params

{'MACD_fast_period': 22,
 'MACD_slow_period': 34,
 'MACD_signal_period': 9,
 'BB_n_periods': 22,
 'BB_n_std_for_long': 2.538280029078493,
 'BB_n_std_for_short': 3.0000000000000018,
 'RSI_n_periods': 14,
 'RSI_overbought_threshold': 77,
 'use_BB_for_long': 0,
 'use_BB_for_short': 1,
 'use_RSI_for_SHORT': 0,
 'use_MACD_for_LONG': 1,
 'use_MACD_for_SHORT': 1,
 'trailing_sl_ATR': 5}

### Run

After optimization, this step runs the backtest using the best-performing parameters found in the optimization phase. The results of the backtest are then plotted using `bt1.plot()`. The first plot is saved as an HTML file with the ticker name, and the second plot is displayed directly in the notebook.

In [ ]:
bt1.plot(filename=f"{Config.ticker}_backtest_results.html",superimpose= False)
bt1.plot(superimpose = False)

GridPlot(id='p1929', ...)

# Automated Backtesting

This section allows you to perform backtesting on a list of tickers in an automated fashion using multiprocessing.

## Download a List of Tickers Data

Download historical data for a predefined list of tickers using `yfinance`. The code includes error handling for tickers that may not have data.

In [ ]:
ticker_list = ["0332.HK","0333.HK","0334.HK","0335.HK","0336.HK","0337.HK","0338.HK","0339.HK","0340.HK","0341.HK","0343.HK","0345.HK","0346.HK","0347.HK","0348.HK","0351.HK","0352.HK","0353.HK","0354.HK","0355.HK","0356.HK","0357.HK","0358.HK","0360.HK","0361.HK","0362.HK","0363.HK","0365.HK","0366.HK","0367.HK","0368.HK","0369.HK","0370.HK",\
               "0371.HK","0372.HK","0373.HK","0374.HK","0375.HK","0376.HK","0377.HK","0379.HK","0380.HK","0381.HK","0382.HK","0383.HK","0384.HK","0385.HK","0386.HK","0387.HK","0388.HK","0389.HK","0390.HK","0391.HK","0392.HK","0393.HK","0396.HK","0397.HK","2535.HK","2536.HK","2540.HK","2545.HK","2549.HK","2550.HK","2551.HK","2552.HK","2555.HK",\
               "2556.HK","2558.HK","2559.HK","2560.HK","2562.HK","5419.HK","5420.HK","5421.HK","5422.HK","5423.HK","5424.HK","5425.HK","5426.HK","5428.HK","5429.HK","5430.HK","5433.HK","5434.HK","5435.HK","7855.HK","8001.HK","8003.HK","8005.HK","8006.HK","8007.HK","8013.HK","8017.HK","8018.HK","8019.HK","8020.HK","8021.HK","8023.HK","8026.HK",\
               "8027.HK","8028.HK","8029.HK","8030.HK","8031.HK","8033.HK","8035.HK","8036.HK","8037.HK","8039.HK","8040.HK","8041.HK","8042.HK","8043.HK","8115.HK","8117.HK","8118.HK","8120.HK","8121.HK","8123.HK","8125.HK","8126.HK","8128.HK","8130.HK","8131.HK","8132.HK","8133.HK","8136.HK",]
start = Config.start
end = Config.end

def prepare_yfinance_df(df):
    """
    Converts the index of a Yahoo Finance DataFrame to datetime
    and removes the multi-level column index if present.

    Args:
        df (pd.DataFrame): The DataFrame downloaded from yfinance.

    Returns:
        pd.DataFrame: The processed DataFrame with a datetime index.
    """
    import pandas as pd
    # Convert index to DatetimeIndex
    df.index = pd.to_datetime(df.index)
    # Remove multi-level column index if present
    if isinstance(df.columns, pd.MultiIndex):
        df.columns = df.columns.droplevel(1)
    return df

def process_ticker(tick, dfs):
    try:
        return tick, prepare_yfinance_df(dfs[tick]).dropna()
    except Exception as e:
        print(f"Error processing ticker {tick}: {e}")
        return tick, None

if __name__ == "__main__": # Required for multiprocessing on Windows
    dfs = yf.download(ticker_list, start, end, auto_adjust = True, threads=True, group_by='ticker')
    ticker_list = dfs.columns.get_level_values(0).unique()
    with multiprocessing.Pool(processes=multiprocessing.cpu_count()) as pool:  # Use all available cores
        ticker_df_list = pool.starmap(process_ticker, [(tick, dfs) for tick in ticker_list])

        # Filter out any failed tickers if you returned None in process_ticker
        ticker_df_list = [item for item in ticker_df_list if item[1] is not None]

[**********************53%                       ]  67 of 127 completedERROR:yfinance:Failed to get ticker '0383.HK' reason: Failed to perform, curl: (28) Connection timed out after 10002 milliseconds. See https://curl.se/libcurl/c/libcurl-errors.html first for more details.
[**********************72%**********             ]  92 of 127 completedERROR:yfinance:Failed to get ticker '8013.HK' reason: Failed to perform, curl: (28) Operation timed out after 10002 milliseconds with 0 bytes received. See https://curl.se/libcurl/c/libcurl-errors.html first for more details.
[*********************100%***********************]  127 of 127 completed
ERROR:yfinance:
14 Failed downloads:
ERROR:yfinance:['5419.HK', '5426.HK', '5421.HK', '5428.HK', '5424.HK', '5434.HK', '5420.HK', '5423.HK', '5429.HK', '5425.HK', '5435.HK', '5433.HK', '5430.HK', '5422.HK']: YFPricesMissingError('possibly delisted; no price data found  (1d 2024-01-01 -> 2025-07-31 17:27:52.275135)')


## Optional: Filtering

Filter the downloaded ticker data based on criteria such as trading volume and closing price.

In [ ]:
def process_ticker(ticker_df_tuple):
    """Processes a single ticker and its DataFrame."""
    ticker, df = ticker_df_tuple
    average_volume = df['Volume'].iloc[-10:].mean()
    if (average_volume > 8000000 and
        df['Close'].iloc[-1] < 3
        ) :
        return (ticker, df)
    return None

def get_valid_tickers(ticker_df_list):
    """Processes a list of (ticker, DataFrame) tuples in parallel."""
    with multiprocessing.Pool(processes=multiprocessing.cpu_count()) as pool:
        results = pool.map(process_ticker, ticker_df_list)

    target_dfs = [result for result in results if result is not None]
    return target_dfs


valid_tickers = get_valid_tickers(ticker_df_list)

print(f"{len(valid_tickers)} Valid Tickers")
print([i[0] for i in valid_tickers])

10 Valid Tickers
['0340.HK', '0347.HK', '0337.HK', '0332.HK', '8123.HK', '0371.HK', '8017.HK', '8021.HK', '0397.HK', '0338.HK']


## Iteratively Running: Multi Processing

Define the trading strategy (similar to the single ticker section). The `process_stock` function performs the backtest and optimization for a single ticker. This function is then mapped to the list of valid tickers using a multiprocessing pool to run backtests in parallel. The results of each backtest are saved as HTML files.

### Strategy 1

#### Define Strategy

In [ ]:
class MyStrategy(TrailingStrategy):
    MACD_fast_period = 12
    MACD_slow_period = 26
    MACD_signal_period = 9

    BB_n_periods = 20
    BB_n_std_for_long = 2
    BB_n_std_for_short = 2

    RSI_n_periods = 14

    RSI_overbought_threshold = 80
    use_BB_for_long = 1
    use_BB_for_short = 1
    use_RSI_for_SHORT = 1
    use_RSI_for_LONG = 1
    use_MACD_for_LONG = 1
    use_MACD_for_SHORT = 1
    trailing_sl_ATR = 2  # Example trailing stop ATR multiplier

    def init(self):
        super().init()
        # MACD Calculation
        self.macd, self.macd_signal, self.macd_hist = self.I(talib.MACD, self.data.Close,
                                                             fastperiod=self.MACD_fast_period,
                                                             slowperiod=self.MACD_slow_period,
                                                             signalperiod=self.MACD_signal_period,
                                                             plot = False
                                                             )
        self.upper, self.middle, self.lower = self.I(talib.BBANDS, self.data.Close,
                                                    timeperiod=self.BB_n_periods,
                                                    nbdevup=self.BB_n_std_for_short,
                                                    nbdevdn=self.BB_n_std_for_long,
                                                    plot = True)
        def get_user_macd(macd, macd_signal, macd_hist):
            return macd, macd_signal, macd_hist
        self.macd, self.macd_signal, self.macd_hist = self.I(get_user_macd, self.macd, self.macd_signal, self.macd_hist)
        # Calculate RSI
        self.rsi = self.I(talib.RSI, self.data.Close, timeperiod=self.RSI_n_periods)

        self.FINAL_SIGNAL = None  # For debugging/analysis

    def next(self):
        super().next()
        # Buy when MACD signal crosses BELOW lower Bollinger Band
        macd_buy = self.macd_signal[-1] < self.lower[-1]

        # Sell when MACD signal crosses ABOVE upper Bollinger Band
        macd_sell = self.macd_signal[-1] > self.lower[-1]
        BB_buy = self.data.Close[-1] > self.upper[-1]
        BB_sell = self.data.Close[-1] < self.lower[-1]

        rsi_overbought = self.rsi[-1] > self.RSI_overbought_threshold
        rsi_oversold = self.rsi[-1] < 20

        buy_signal = (
            (self.use_MACD_for_LONG and macd_buy) or
            (self.use_BB_for_long and BB_buy) or
            (self.use_RSI_for_LONG and rsi_oversold)
            )

        sell_signal = (
            (self.use_MACD_for_SHORT and macd_sell) or
            (self.use_BB_for_short and BB_sell) or
            (self.use_RSI_for_SHORT and rsi_overbought)
        )

        if self.position:
            if sell_signal:
                self.position.close()
                self.FINAL_SIGNAL = -1  # Mark as sell
        elif buy_signal:
            self.buy()
            self.FINAL_SIGNAL = 1  # Mark as buy

        if self.position:  # Only set trailing stop if in a position
            self.set_trailing_sl(self.trailing_sl_ATR)  # Set trailing stop loss

#### Auto Processing

In [ ]:
def process_stock(stock_data):
    stock_name, stock_df = stock_data
    df1 = stock_df

    try:
        bt1 = Backtest(df1, MyStrategy, cash=Config.cash, finalize_trades = Config.finalize_trades)
        stats, heatmap, optimize_result = bt1.optimize(
            MACD_fast_period = range(12, 18, 2),
            MACD_slow_period = range(24,30, 2),
            MACD_signal_period = range(3,10,2),

            BB_n_periods = range(15,25,2),
            BB_n_std_for_long = np.arange(1, 3.1, 0.1),
            BB_n_std_for_short = np.arange(1, 3.1, 0.1),
            RSI_n_periods = np.arange(14,16,2),
            RSI_overbought_threshold = np.arange(75, 96, 5),

            use_BB_for_long = [1,0],
            use_BB_for_short = [1,0],
            use_RSI_for_SHORT = [1,0],
            use_MACD_for_LONG = [1],
            use_MACD_for_SHORT = [1],
            trailing_sl_ATR = [2,3,4,5],
            maximize=Config.maximize,
            method=Config.method,
            max_tries=Config.max_tries,
            random_state=Config.random_state,
            return_heatmap=Config.return_heatmap,
            return_optimization=Config.return_optimization,
        )


        bt1.plot(filename=f"{stock_name.replace('.','_')}_backtest_results.html", superimpose=False)
        del bt1

    except Exception as e:
        print(f"Error occurred for ticker {stock_name}: {e}")
        del bt1



# Determine the number of processes to use (usually number of CPU cores)
num_processes = os.cpu_count()

# Create a Pool of workers
with Pool(processes=num_processes) as pool:
    # Map the process_stock function to all stocks in parallel
    results = pool.map(process_stock, valid_tickers)

## Example Results

In [ ]:
backtest_htmls = []
for path in os.listdir():
    if path.endswith(".html"):
        backtest_htmls.append(path)
        print(path)
print(f"\nThere are {len(backtest_htmls)} Backtest Results")

0371_HK_backtest_results.html
0332_HK_backtest_results.html
AAPL_backtest_results.html
0347_HK_backtest_results.html
0338_HK_backtest_results.html
0340_HK_backtest_results.html
8021_HK_backtest_results.html
8017_HK_backtest_results.html
0337_HK_backtest_results.html
8123_HK_backtest_results.html
0397_HK_backtest_results.html

There are 11 Backtest Results
